In [1]:
from elasticsearch import Elasticsearch
from datetime import datetime
import elasticsearch.helpers
from elasticsearch_dsl import Search, A, Q
from elasticsearch_dsl.query import MultiMatch, Match
import pandas as pd
import json

In [3]:
es = Elasticsearch("http://localhost:9200")

In [4]:
es.info()

{'name': 'd37ce438b9f7',
 'cluster_name': 'docker-cluster',
 'cluster_uuid': 'er6OnL0vQQSkJRghX1tyBA',
 'version': {'number': '8.2.2',
  'build_flavor': 'default',
  'build_type': 'docker',
  'build_hash': '9876968ef3c745186b94fdabd4483e01499224ef',
  'build_date': '2022-05-25T15:47:06.259735307Z',
  'build_snapshot': False,
  'lucene_version': '9.1.0',
  'minimum_wire_compatibility_version': '7.17.0',
  'minimum_index_compatibility_version': '7.0.0'},
 'tagline': 'You Know, for Search'}

In [6]:
es.indices.create(index='my_first_index')

{'acknowledged': True, 'shards_acknowledged': True, 'index': 'my_first_index'}

In [4]:
es.indices.exists(index='my_first_index')

True

In [10]:
# es.indices.delete(index='my_sec_index')

In [1]:
def insert_a_list_of_doc(connection, index_name, list_of_doc, start_id=None):
    counter = start_id
    
    for doc in list_of_doc:
        if counter is not None:
            connection.index(index=index_name, id=counter, document=doc)
            counter +=1
        else:
            connection.index(index=index_name, document=doc)

In [114]:
def get_aggregate_result(connection, index_name, agg_content, query_content=None, size=0):
    respond = connection.search(index=index_name, aggs=agg_content, query=query_content, size=size)
    
    return respond['aggregations'][list(es_aggs.keys())[0]]

In [116]:
def extract_to_df(connection, index_name, query_content, score_require=False):
    results = elasticsearch.helpers.scan(connection,
    query=query_content,
    index=index_name,
    preserve_order = score_require
)
    if score_require:
        return pd.DataFrame.from_dict([{**document['_source'], **{'_score': document['_score']}} for document in results])
    else:
        return pd.DataFrame.from_dict([document['_source'] for document in results])

In [45]:
es_query = {"range": {
    "date": {
        "gte": "2015-06-20",
        "lte": "2015-09-22"
      }
    }
           }

data = es.search(index='news_headlines', query=es_query, size='0')



In [115]:
es_aggs =  {
    "transactions_by_8_hrs": {
      "date_histogram": {
        "field": "InvoiceDate",
        "fixed_interval": "8h"
      }
    }
  }

data = es.search(index='ecommerce_data', aggs=es_aggs, size=0)


In [99]:
es_aggs =  {"sum_unit_price": {
    "sum": {
        "field": "UnitPrice"
      }
    }
            }

In [111]:
es_aggs.keys()
#list(es_aggs.keys())[0]

dict_keys(['sum_unit_price'])

In [87]:
data

{'took': 83,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 10000, 'relation': 'gte'},
  'max_score': None,
  'hits': []},
 'aggregations': {'sum_unit_price': {'value': 1946449.894}}}

In [94]:
es_query = {
    "match": {
      "Country": "Germany"
    }
}
    
es_aggs = {
    "germany_average_unit_price": {
      "avg": {
        "field": "UnitPrice"
      }
    }
}

data = es.search(index='ecommerce_data', aggs=None, query=None)

In [95]:
data

{'took': 5,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 10000, 'relation': 'gte'},
  'max_score': 1.0,
  'hits': [{'_index': 'ecommerce_data',
    '_id': 'eMyK1oEBT6T2g4AyzoiY',
    '_score': 1.0,
    '_source': {'UnitPrice': 5.91,
     'Description': 'HANGING MEDINA LANTERN SMALL',
     'Quantity': 2,
     'Country': 'United Kingdom',
     'InvoiceNo': '540977',
     'InvoiceDate': '1/12/2011 15:01',
     'StockCode': '21324'}},
   {'_index': 'ecommerce_data',
    '_id': 'ecyK1oEBT6T2g4AyzoiY',
    '_score': 1.0,
    '_source': {'UnitPrice': 5.91,
     'Description': 'BLUE TV TRAY TABLE ',
     'Quantity': 1,
     'Country': 'United Kingdom',
     'InvoiceNo': '540977',
     'InvoiceDate': '1/12/2011 15:01',
     'StockCode': '84313B'}},
   {'_index': 'ecommerce_data',
    '_id': 'esyK1oEBT6T2g4AyzoiY',
    '_score': 1.0,
    '_source': {'UnitPrice': 3.36,
     'Description': 'DINOSAURS  WRITING SET ',
     'Q

In [44]:
len(data['hits']['hits'])

100

In [27]:
def process_hits(hits):
    for item in hits:
        print(json.dumps(item, indent=2))

In [30]:
while scroll_size > 0:
    "Scrolling..."
    
    # Before scroll, process current batch of hits
    process_hits(data['hits']['hits'])
    
    data = es.scroll(scroll_id=sid, scroll='2m')

    # Update the scroll ID
    sid = data['_scroll_id']

    # Get the number of results that returned in the last scroll
    scroll_size = len(data['hits']['hits'])

{
  "_index": "news_headlines",
  "_id": "c8mD0oEBT6T2g4Ay3tda",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-22",
    "short_description": "German publishing giant Axel Springer is closing in on a deal to buy Business Insider, in a deal that would value the Web",
    "@timestamp": "2015-09-22T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.comhttp://recode.net/2015/09/21/axel-springer-wants-to-buy-business-insider-for-around-560-million/",
    "category": "MEDIA",
    "headline": "Report: Axel Springer Eyes Purchase Of Business Insider For $560 Million",
    "authors": ""
  }
}
{
  "_index": "news_headlines",
  "_id": "dMmD0oEBT6T2g4Ay3tda",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-22",
    "short_description": "Dad to the rescue.",
    "@timestamp": "2015-09-22T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/adorable-kid-has-a-hard-time-blowing-out-his-birthday-candle_us_56018127e4b00310edf8a7d2",
    "category": "PARENTS",
    

{
  "_index": "news_headlines",
  "_id": "qcmD0oEBT6T2g4Ay3tha",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-19",
    "short_description": "Pope Francis began a 10-day trip to Cuba and the United States on Saturday, embarking on his first trip to the onetime Cold",
    "@timestamp": "2015-09-19T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/pope-solidarity-cubans_us_55fd6c33e4b00310edf7425a",
    "category": "RELIGION",
    "headline": "Pope To Offer Solidarity With Cubans On Trip To U.S.",
    "authors": "Nicole Winfield and Michael Weissenstein, AP"
  }
}
{
  "_index": "news_headlines",
  "_id": "qsmD0oEBT6T2g4Ay3tha",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-19",
    "short_description": "\"At that moment, we, all of us, thought that we are useless, we are not human.\"",
    "@timestamp": "2015-09-19T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/girl-dead-refugee-boat-greece_us_55fd7254e4b00310edf74294",
    "cate

{
  "_index": "news_headlines",
  "_id": "ncmD0oEBT6T2g4Ay4tr2",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-14",
    "short_description": "Seriously, half a decade for marijuana.",
    "@timestamp": "2015-09-14T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/nick-diaz-marijuana-r-u-kidding-me_us_55f74c6fe4b00e2cd5e7bda4",
    "category": "SPORTS",
    "headline": "UFC Fighter Suspended 5 Years For...Wait, What? Smoking Weed?!",
    "authors": "Maxwell Strachan"
  }
}
{
  "_index": "news_headlines",
  "_id": "nsmD0oEBT6T2g4Ay4tr2",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-14",
    "short_description": "\"Why must I type this?\"",
    "@timestamp": "2015-09-14T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/chrissy-teigen-no-hot-nannies-twitter_us_55f70db4e4b063ecbfa521f9",
    "category": "ENTERTAINMENT",
    "headline": "Chrissy Teigen Defends 'No Hot Nannies' Comment On Twitter",
    "authors": "Julia Brucculieri"
  }

{
  "_index": "news_headlines",
  "_id": "r8mD0oEBT6T2g4Ay4tz3",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-08",
    "short_description": "The judge also ordered the defiant clerk not to interfere with the work of other deputies in Rowan County.",
    "@timestamp": "2015-09-08T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/federal-judge-orders-immediate-release-of-kim-davis_us_55ef12b7e4b03784e2769a9f",
    "category": "POLITICS",
    "headline": "Federal Judge Orders Immediate Release of Kentucky Clerk Kim Davis",
    "authors": "Cristian Farias"
  }
}
{
  "_index": "news_headlines",
  "_id": "sMmD0oEBT6T2g4Ay4tz3",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-08",
    "short_description": "An attorney for the jailed county clerk isn't sure the Supreme Court can rule on the Constitution.",
    "@timestamp": "2015-09-08T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/fox-news-kim-davis_us_55eee6e8e4b03784e27665d9",
    "c

{
  "_index": "news_headlines",
  "_id": "rcmD0oEBT6T2g4Ay4t73",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-02",
    "short_description": "If you want to pay for it, that is.",
    "@timestamp": "2015-09-02T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/finally-hulu-is-ad-free_us_55e77279e4b0c818f61a9113",
    "category": "ENTERTAINMENT",
    "headline": "Finally, You Can Now Watch Hulu Without Ads",
    "authors": "Sara Boboltz"
  }
}
{
  "_index": "news_headlines",
  "_id": "rsmD0oEBT6T2g4Ay4t73",
  "_score": 1.0,
  "_source": {
    "date": "2015-09-02",
    "short_description": "But the university isn't hiding its annoyance with the lengthy investigation.",
    "@timestamp": "2015-09-02T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/michigan-state-title-ix_us_55e5fef5e4b0c818f619714f",
    "category": "COLLEGE",
    "headline": "Michigan State Took Too Long With Sexual Assault Cases, Federal Investigation Finds",
    "authors

...

{
  "_index": "news_headlines",
  "_id": "Y8mD0oEBT6T2g4Ay4uL4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-22",
    "short_description": "Business isn't simple; foreign policy isn't either. If Trump wants to be taken seriously by the general electorate, he should demonstrate the nuanced understanding of foreign policy exemplified by candidates ranging from Jeb Bush to Hillary Clinton.",
    "@timestamp": "2015-08-22T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/trump-excels-at-business-_b_8018654.html",
    "category": "ENTERTAINMENT",
    "headline": "Trump Excels at Business, But He Has No Business in International Politics",
    "authors": "Michael Shammas, ContributorLawyer, freelancer, writer"
  }
}
{
  "_index": "news_headlines",
  "_id": "ZMmD0oEBT6T2g4Ay4uL4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-22",
    "short_description": "Dear Anna, there will be Christian voices that will say you need to stay with Josh.  They will tell y

{
  "_index": "news_headlines",
  "_id": "dcmD0oEBT6T2g4Ay5-R3",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-16",
    "short_description": "Of course it felt a bit like an outpost of the gorgeous museum in Paris -- but without seeming imitative or second best.  This museum had its own special grace and logic.",
    "@timestamp": "2015-08-16T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/european-vacation--in-phi_b_7958790.html",
    "category": "TRAVEL",
    "headline": "European Vacation -- in Philadelphia!",
    "authors": "Lev Raphael, ContributorAuthor, reviewer, and blogger"
  }
}
{
  "_index": "news_headlines",
  "_id": "dsmD0oEBT6T2g4Ay5-R3",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-16",
    "short_description": "To all the kids going away to college this fall, from the parents who have been feeding them: We love you. Come back for snacks.",
    "@timestamp": "2015-08-16T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com

{
  "_index": "news_headlines",
  "_id": "h8mD0oEBT6T2g4Ay5-Z4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-10",
    "short_description": "The only real mystery was why we spent eight and a half hours on this.",
    "@timestamp": "2015-08-10T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/huffpost-live-spoiler-alert-true-detective-finale_us_55c8f6efe4b0923c12bdb4b9",
    "category": "ENTERTAINMENT",
    "headline": "An Autopsy For The Dismal Second Season Of 'True Detective'",
    "authors": "Ryan Buxton"
  }
}
{
  "_index": "news_headlines",
  "_id": "iMmD0oEBT6T2g4Ay5-Z4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-10",
    "short_description": "The Star Tribune's Amelia Rayno shares her chilling story.",
    "@timestamp": "2015-08-10T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.comhttp://www.startribune.com/star-tribune-s-rayno-adds-her-own-story-to-teague-scandal/321199871/",
    "category": "SPORTS",
    "headline": "Repor

{
  "_index": "news_headlines",
  "_id": "ScmD0oEBT6T2g4Ay5-h4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-05",
    "short_description": "Will their rumored romance save us from the summer of celebrity splits?",
    "@timestamp": "2015-08-05T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/kendall-jenner-nick-jonas-dating_us_55c2465de4b0138b0bf4ba44",
    "category": "ENTERTAINMENT",
    "headline": "Kendall Jenner And Nick Jonas Are Reportedly Dating",
    "authors": "Stephanie Marcus"
  }
}
{
  "_index": "news_headlines",
  "_id": "SsmD0oEBT6T2g4Ay5-h4",
  "_score": 1.0,
  "_source": {
    "date": "2015-08-05",
    "short_description": "The stunt by Florida mailman Douglas Hughes showed the need for improved information-sharing and air security technology, the report from the Senate Homeland Security and Governmental Affairs Committee said.",
    "@timestamp": "2015-08-05T00:00:00.000+08:00",
    "link": "https://www.huffingtonpost.com/entry/capitol-g

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [24]:
sid = data['_scroll_id']

In [25]:
scroll_size = len(data['hits']['hits'])

In [26]:
scroll_size

10

In [20]:
len(results['hits']['hits'])

10

In [36]:
es_query = {
    "size": 5,
    "query":{
        "range": {
            "date": {
                "gte": "2015-06-20",
                "lte": "2015-09-22"
            }
        }
    }
}

In [70]:
es_query = {
    "size": 5,
    "query":{
        "match": {
            "headline": "Robot"
        }
    }
}

In [96]:
es_query = {
  "size": 0,
  "query": {
    "match": {
      "Country": "Germany"
    }
  },
  "aggs": {
    "germany_average_unit_price": {
      "avg": {
        "field": "UnitPrice"
      }
    }
  }
}

In [97]:
results = elasticsearch.helpers.scan(es,
    query=es_query,
    index='ecommerce_data',
    preserve_order = True
)

In [98]:
for item in results:
    print(item)

{'_index': 'ecommerce_data', '_id': 'NcyK1oEBT6T2g4Ayzo2Z', '_score': None, '_source': {'Description': 'TV DINNER TRAY DOLLY GIRL', 'Quantity': 3, 'InvoiceNo': '541093', 'CustomerID': 12471, 'UnitPrice': 4.95, 'Country': 'Germany', 'InvoiceDate': '1/13/2011 13:21', 'StockCode': '22472'}, 'sort': [330009]}
{'_index': 'ecommerce_data', '_id': 'NsyK1oEBT6T2g4Ayzo2Z', '_score': None, '_source': {'Description': 'PENCIL CASE LIFE IS BEAUTIFUL', 'Quantity': 6, 'InvoiceNo': '541093', 'CustomerID': 12471, 'UnitPrice': 2.95, 'Country': 'Germany', 'InvoiceDate': '1/13/2011 13:21', 'StockCode': '22445'}, 'sort': [330010]}
{'_index': 'ecommerce_data', '_id': 'OcyK1oEBT6T2g4Ayzo2Z', '_score': None, '_source': {'Description': 'BAKING MOULD CHOCOLATE CUPCAKES', 'Quantity': 18, 'InvoiceNo': '541093', 'CustomerID': 12471, 'UnitPrice': 2.55, 'Country': 'Germany', 'InvoiceDate': '1/13/2011 13:21', 'StockCode': '22937'}, 'sort': [330013]}
{'_index': 'ecommerce_data', '_id': 'OsyK1oEBT6T2g4Ayzo2Z', '_score'

{'_index': 'ecommerce_data', '_id': 'Ws2L1oEBT6T2g4AyA_tu', '_score': None, '_source': {'Description': 'ALARM CLOCK BAKELIKE PINK', 'Quantity': 8, 'InvoiceNo': '549316', 'CustomerID': 12705, 'UnitPrice': 3.75, 'Country': 'Germany', 'InvoiceDate': '4/8/2011 9:54', 'StockCode': '22728'}, 'sort': [564735]}
{'_index': 'ecommerce_data', '_id': 'W82L1oEBT6T2g4AyA_tu', '_score': None, '_source': {'Description': 'GUMBALL COAT RACK', 'Quantity': 36, 'InvoiceNo': '549316', 'CustomerID': 12705, 'UnitPrice': 2.1, 'Country': 'Germany', 'InvoiceDate': '4/8/2011 9:54', 'StockCode': '22467'}, 'sort': [564736]}
{'_index': 'ecommerce_data', '_id': 'XM2L1oEBT6T2g4AyA_tu', '_score': None, '_source': {'Description': 'JUNGLE POPSICLES ICE LOLLY MOULDS', 'Quantity': 12, 'InvoiceNo': '549316', 'CustomerID': 12705, 'UnitPrice': 1.25, 'Country': 'Germany', 'InvoiceDate': '4/8/2011 9:54', 'StockCode': '84828'}, 'sort': [564737]}
{'_index': 'ecommerce_data', '_id': 'Xc2L1oEBT6T2g4AyA_tu', '_score': None, '_source

{'_index': 'ecommerce_data', '_id': '786L1oEBT6T2g4AyN8U7', '_score': None, '_source': {'Description': '3 HOOK HANGER MAGIC GARDEN', 'Quantity': 12, 'InvoiceNo': '554325', 'CustomerID': 12621, 'UnitPrice': 1.95, 'Country': 'Germany', 'InvoiceDate': '5/23/2011 15:38', 'StockCode': '22244'}, 'sort': [616596]}
{'_index': 'ecommerce_data', '_id': '8M6L1oEBT6T2g4AyN8U7', '_score': None, '_source': {'Description': 'PACK OF 72 RETROSPOT CAKE CASES', 'Quantity': 24, 'InvoiceNo': '554325', 'CustomerID': 12621, 'UnitPrice': 0.55, 'Country': 'Germany', 'InvoiceDate': '5/23/2011 15:38', 'StockCode': '21212'}, 'sort': [616597]}
{'_index': 'ecommerce_data', '_id': '8c6L1oEBT6T2g4AyN8U7', '_score': None, '_source': {'Description': 'PINK/PURPLE RETRO RADIO', 'Quantity': 6, 'InvoiceNo': '554325', 'CustomerID': 12621, 'UnitPrice': 2.95, 'Country': 'Germany', 'InvoiceDate': '5/23/2011 15:38', 'StockCode': '84086C'}, 'sort': [616598]}
{'_index': 'ecommerce_data', '_id': '8s6L1oEBT6T2g4AyN8U7', '_score': N

{'_index': 'ecommerce_data', '_id': 'y9CL1oEBT6T2g4Ayg6iO', '_score': None, '_source': {'Description': 'ALARM CLOCK BAKELIKE IVORY', 'Quantity': 4, 'InvoiceNo': '565440', 'CustomerID': 12709, 'UnitPrice': 3.75, 'Country': 'Germany', 'InvoiceDate': '9/4/2011 14:06', 'StockCode': '22730'}, 'sort': [786328]}
{'_index': 'ecommerce_data', '_id': 'zNCL1oEBT6T2g4Ayg6iO', '_score': None, '_source': {'Description': 'PARTY BUNTING', 'Quantity': 8, 'InvoiceNo': '565440', 'CustomerID': 12709, 'UnitPrice': 4.95, 'Country': 'Germany', 'InvoiceDate': '9/4/2011 14:06', 'StockCode': '47566'}, 'sort': [786329]}
{'_index': 'ecommerce_data', '_id': 'zdCL1oEBT6T2g4Ayg6iO', '_score': None, '_source': {'Description': 'MINT KITCHEN SCALES', 'Quantity': 10, 'InvoiceNo': '565440', 'CustomerID': 12709, 'UnitPrice': 8.5, 'Country': 'Germany', 'InvoiceDate': '9/4/2011 14:06', 'StockCode': '22627'}, 'sort': [786330]}
{'_index': 'ecommerce_data', '_id': 'ztCL1oEBT6T2g4Ayg6iO', '_score': None, '_source': {'Descriptio

{'_index': 'ecommerce_data', '_id': 'YtOL1oEBT6T2g4Ay7E8G', '_score': None, '_source': {'Description': 'ALARM CLOCK BAKELIKE GREEN', 'Quantity': 8, 'InvoiceNo': '578626', 'CustomerID': 12709, 'UnitPrice': 3.75, 'Country': 'Germany', 'InvoiceDate': '11/24/2011 15:38', 'StockCode': '22726'}, 'sort': [960047]}
{'_index': 'ecommerce_data', '_id': 'Y9OL1oEBT6T2g4Ay7E8G', '_score': None, '_source': {'Description': 'ALARM CLOCK BAKELIKE PINK', 'Quantity': 8, 'InvoiceNo': '578626', 'CustomerID': 12709, 'UnitPrice': 3.75, 'Country': 'Germany', 'InvoiceDate': '11/24/2011 15:38', 'StockCode': '22728'}, 'sort': [960048]}
{'_index': 'ecommerce_data', '_id': 'ZNOL1oEBT6T2g4Ay7E8G', '_score': None, '_source': {'Description': 'PACK OF 20 NAPKINS PANTRY DESIGN', 'Quantity': 24, 'InvoiceNo': '578626', 'CustomerID': 12709, 'UnitPrice': 0.85, 'Country': 'Germany', 'InvoiceDate': '11/24/2011 15:38', 'StockCode': '22907'}, 'sort': [960049]}
{'_index': 'ecommerce_data', '_id': 'ZdOL1oEBT6T2g4Ay7E8G', '_score

In [71]:
results = elasticsearch.helpers.scan(es,
    query=es_query,
    index='news_headlines',
    preserve_order = True
)

In [38]:
my_list = []
for _ in results:
    my_list.append(_)

In [72]:
df = pd.DataFrame.from_dict([{**document['_source'], **{'_score': document['_score']}} for document in results])

In [66]:
df = pd.DataFrame.from_dict([document['_source'] for document in results])

In [67]:
df

date                                  short_description  \
0   2015-08-25                01001100 01101111 01110110 01100101   
1   2013-08-18  We're not sure why this is so charming, but we...   
2   2016-02-25                                Cruel, cruel human.   
3   2015-10-13          What is it and what does it want from us?   
4   2015-09-09  A drunk guy in a cellphone store in Japan was ...   
..         ...                                                ...   
94  2016-09-19  Bag containing explosive devices was found in ...   
95  2016-01-11       Celebrating the best Hollywood has to offer.   
96  2017-03-13                        This loss does not compute.   
97  2015-08-01  But fans can expect an answer to their biggest...   
98  2016-10-02       The hackers definitely aren't who you think.   

                       @timestamp  \
0   2015-08-25T00:00:00.000+08:00   
1   2013-08-18T00:00:00.000+08:00   
2   2016-02-25T00:00:00.000+08:00   
3   2015-10-13T00:00:00.000+08:00   
4   2015-09-09T00:00:00.000+08:00   
..                            ...   
94  2016-09-19T00:00:00.000+08:00   
95  2016-01-11T00:00:00.000+08:00   
96  2017-03-13T00:00:00.000+08:00   
97  2015-08-01T00:00:00.000+08:00   
98  2016-10-02T00:00:00.000+08:00   

                                                 link       category  \
0   https://www.huffingtonpost.com/entry/robot-can...         COMEDY   
1   https://www.huffingtonpost.com/entry/little-ro...         COMEDY   
2   https://www.huffingtonpost.com/entry/human-bul...           TECH   
3   https://www.huffingtonpost.com/entry/all-fear-...     WEIRD NEWS   
4   https://www.huffingtonpost.comhttp://pubx.ch/1...     WEIRD NEWS   
..                                                ...            ...   
94  https://www.huffingtonpost.com/entry/suspiciou...          CRIME   
95  https://www.huffingtonpost.com/entry/golden-gl...  ENTERTAINMENT   
96  https://www.huffingtonpost.com/entry/man-has-a...  ENTERTAINMENT   
97  https://www.huffingtonpost.com/entry/mr-robot-...  ENTERTAINMENT   
98  https://www.huffingtonpost.com/entry/leslie-jo...  ENTERTAINMENT   

                                             headline            authors  
0   'To The People Saying I'm A Robot Who Can't Lo...      Andy McDonald  
1                 Little Robot Fights Kittens (VIDEO)                     
2       Bearded Human Bullies Poor, Defenseless Robot     Casey Williams  
3                          All Fear 'Toad On A Robot'      Steven Hoffer  
4             Drunk Man Arrested For Assaulting Robot                     
..                                                ...                ...  
94  'Suspicious Package' Explodes In New Jersey As...    Rebecca Shapiro  
95  Golden Globes 2016 Winners Include Leonardo Di...   Stephanie Marcus  
96  Here's Why A Grown Man Walked Off Set After Lo...       Bill Bradley  
97  'Mr. Robot' Creator Also Thinks It's Weird Tha...       Sara Boboltz  
98  Leslie Jones Enlists 'Mr. Robot' Crew To Help ...  Julia Brucculieri  

[99 rows x 7 columns]

In [60]:
df

Empty DataFrame
Columns: []
Index: []

In [56]:
df.iloc[1]['authors']

''

In [39]:
len(my_list)

8388

In [48]:
{**{'a':123, 'b':234}, **{'c':456}}

{'a': 123, 'b': 234, 'c': 456}

In [40]:
my_list

[{'_index': 'news_headlines',
  '_id': 'c8mD0oEBT6T2g4Ay3tda',
  '_score': 1.0,
  '_source': {'date': '2015-09-22',
   'short_description': 'German publishing giant Axel Springer is closing in on a deal to buy Business Insider, in a deal that would value the Web',
   '@timestamp': '2015-09-22T00:00:00.000+08:00',
   'link': 'https://www.huffingtonpost.comhttp://recode.net/2015/09/21/axel-springer-wants-to-buy-business-insider-for-around-560-million/',
   'category': 'MEDIA',
   'headline': 'Report: Axel Springer Eyes Purchase Of Business Insider For $560 Million',
   'authors': ''}},
 {'_index': 'news_headlines',
  '_id': 'dMmD0oEBT6T2g4Ay3tda',
  '_score': 1.0,
  '_source': {'date': '2015-09-22',
   'short_description': 'Dad to the rescue.',
   '@timestamp': '2015-09-22T00:00:00.000+08:00',
   'link': 'https://www.huffingtonpost.com/entry/adorable-kid-has-a-hard-time-blowing-out-his-birthday-candle_us_56018127e4b00310edf8a7d2',
   'category': 'PARENTS',
   'headline': 'Adorable Kid Ha

In [ ]:
df = pd.DataFrame.from_dict([document['_source'] for document in results])

In [12]:
es_query = {"match": {'sentence':'Hack'}}

es.search(index='english', query=es_query)

{'took': 2,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 2, 'relation': 'eq'},
  'max_score': 0.19100355,
  'hits': [{'_index': 'english',
    '_id': '2',
    '_score': 0.19100355,
    '_source': {'sentence': 'Hack-Quarantine is stunning'}},
   {'_index': 'english',
    '_id': '1',
    '_score': 0.17439456,
    '_source': {'sentence': 'Hack COVID-19 is amazing!'}}]}}

In [13]:
es_query = {"match_phrase": {'sentence':'Hack Quarantine'}}

es.search(index='english', query=es_query)

{'took': 47,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 1, 'relation': 'eq'},
  'max_score': 0.91715777,
  'hits': [{'_index': 'english',
    '_id': '2',
    '_score': 0.91715777,
    '_source': {'sentence': 'Hack-Quarantine is stunning'}}]}}

In [15]:
es_query = {"bool": 
            {'must_not':
             {'match':{'sentence':'COVID-19'}}, 
             'should': {'match': {'sentence': 'Hack'}}
            }
           }

es.search(index='english', query=es_query)

{'took': 3,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 1, 'relation': 'eq'},
  'max_score': 0.19100355,
  'hits': [{'_index': 'english',
    '_id': '2',
    '_score': 0.19100355,
    '_source': {'sentence': 'Hack-Quarantine is stunning'}}]}}

In [49]:
es.index(index='sample_logs', document=doc6)
es.index(index='sample_logs', document=doc7)
es.index(index='sample_logs', document=doc8)
es.index(index='sample_logs', document=doc9)

{'_index': 'sample_logs',
 '_id': 'vfuFs4EBga7skXllys4j',
 '_version': 1,
 'result': 'created',
 '_shards': {'total': 2, 'successful': 1, 'failed': 0},
 '_seq_no': 3,
 '_primary_term': 1}

In [101]:
doc10 = {'date': datetime(2022, 1, 1), 'event': 'Today is a sunny day'}
doc11 = {'date': datetime(2022, 3, 1), 'event': 'Today is a hard night'}
doc12 = {'date': datetime(2022, 5, 1), 'event': 'Today is a rainy day'}
doc13 = {'date': datetime(2022, 7, 1), 'event': 'Today is a sad night'}
doc14 = {'date': datetime(2022, 9, 1), 'event': 'Today is a happy day'}
doc15 = {'date': datetime(2022, 11, 1), 'event': 'Today is a cloudy night'}

In [102]:
for doc in [doc10, doc11, doc12, doc13, doc14, doc15]:
    es.index(index='event_log', document=doc)

In [104]:
es.search(index='event_log', query={'match':{'event': 'happy night'}})

{'took': 3,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 4, 'relation': 'eq'},
  'max_score': 1.540445,
  'hits': [{'_index': 'event_log',
    '_id': 'wvsFtIEBga7skXllbs6z',
    '_score': 1.540445,
    '_source': {'date': '2022-09-01T00:00:00',
     'event': 'Today is a happy day'}},
   {'_index': 'event_log',
    '_id': 'v_sFtIEBga7skXllbs6N',
    '_score': 0.6931471,
    '_source': {'date': '2022-03-01T00:00:00',
     'event': 'Today is a hard night'}},
   {'_index': 'event_log',
    '_id': 'wfsFtIEBga7skXllbs6m',
    '_score': 0.6931471,
    '_source': {'date': '2022-07-01T00:00:00',
     'event': 'Today is a sad night'}},
   {'_index': 'event_log',
    '_id': 'w_sFtIEBga7skXllbs69',
    '_score': 0.6931471,
    '_source': {'date': '2022-11-01T00:00:00',
     'event': 'Today is a cloudy night'}}]}}

In [109]:
es.search(index='event_log', query={'range':{'date': {'gte':'2022-01-01', 'lte':'2022-06-30'}}})

{'took': 2,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 3, 'relation': 'eq'},
  'max_score': 1.0,
  'hits': [{'_index': 'event_log',
    '_id': 'vvsFtIEBga7skXllbs42',
    '_score': 1.0,
    '_source': {'date': '2022-01-01T00:00:00',
     'event': 'Today is a sunny day'}},
   {'_index': 'event_log',
    '_id': 'v_sFtIEBga7skXllbs6N',
    '_score': 1.0,
    '_source': {'date': '2022-03-01T00:00:00',
     'event': 'Today is a hard night'}},
   {'_index': 'event_log',
    '_id': 'wPsFtIEBga7skXllbs6Y',
    '_score': 1.0,
    '_source': {'date': '2022-05-01T00:00:00',
     'event': 'Today is a rainy day'}}]}}

In [ ]:
data = [{"balance": "$2,410.62", "age": 40, "name": "Bettie Buckner", "gender": "female", "company": "RODEOMAD",
         "email": "bettiebuckner@rodeomad.com", "phone": "+1 (857) 491-2461"},
        {"balance": "$1,143.56", "age": 28, "name": "Hanson Gates", "gender": "male", "company": "PEARLESSA",
         "email": "hansongates@pearlessa.com", "phone": "+1 (825) 524-3896"},
        {"balance": "$2,542.95", "age": 20, "name": "Audra Marshall", "gender": "female", "company": "COMTRAIL",
         "email": "audramarshall@comtrail.com", "phone": "+1 (920) 569-2780"},
        {"balance": "$2,235.86", "age": 34, "name": "Milagros Conrad", "gender": "female", "company": "IDEGO",
         "email": "milagrosconrad@idego.com", "phone": "+1 (823) 451-2064"},
        {"balance": "$2,606.95", "age": 34, "name": "Maureen Lopez", "gender": "female", "company": "EVENTEX",
         "email": "maureenlopez@eventex.com", "phone": "+1 (913) 425-3716"}]
for a_data in data:
    res = es.index(index='my-index', body=a_data)
    pprint(res)

## DSL

In [5]:
s = Search(using=es, index='news_headlines').filter('range', **{'date':{"gte": "2015-06-20", "lte": "2015-09-22"}})

s = s.params(preserve_order=True).sort("_score")

In [8]:
counter = 0
for item in s.scan():
    print(item.to_dict())
    counter += 1
    if counter > 3:
        break

{'date': '2015-09-22', 'short_description': 'German publishing giant Axel Springer is closing in on a deal to buy Business Insider, in a deal that would value the Web', '@timestamp': '2015-09-22T00:00:00.000+08:00', 'link': 'https://www.huffingtonpost.comhttp://recode.net/2015/09/21/axel-springer-wants-to-buy-business-insider-for-around-560-million/', 'category': 'MEDIA', 'headline': 'Report: Axel Springer Eyes Purchase Of Business Insider For $560 Million', 'authors': ''}
{'date': '2015-09-22', 'short_description': 'Dad to the rescue.', '@timestamp': '2015-09-22T00:00:00.000+08:00', 'link': 'https://www.huffingtonpost.com/entry/adorable-kid-has-a-hard-time-blowing-out-his-birthday-candle_us_56018127e4b00310edf8a7d2', 'category': 'PARENTS', 'headline': 'Adorable Kid Has A Hard Time Blowing Out His Birthday Candle', 'authors': 'Steven Hoffer'}
{'date': '2015-09-22', 'short_description': '"I appreciate that [the sheriff] recognizes that I shouldn\'t have to take off my clothes to see my 

In [7]:
def dsl_query_to_df(search_obj):
    list_of_respond = []
    for doc in search_obj.scan():
        list_of_respond.append({**doc.to_dict(),**{'score':doc.meta.score}})
    
    return pd.DataFrame(list_of_respond)

In [10]:
s = Search(using=es, index='news_headlines')\
    .filter('range', **{'date':{"gte": "2015-06-20", "lte": "2015-09-22"}})\
    .params(preserve_order=True).sort("_score")

dsl_query_to_df(s)

date                                  short_description  \
0     2015-09-22  German publishing giant Axel Springer is closi...   
1     2015-09-22                                 Dad to the rescue.   
2     2015-09-22  "I appreciate that [the sheriff] recognizes th...   
3     2015-09-22  The moral argument for climate action might fi...   
4     2015-09-22  After months of avoiding the subject, Clinton ...   
...          ...                                                ...   
8383  2015-06-20  In a time of great social strife and growing i...   
8384  2015-06-20  When states fail to pass laws that effectively...   
8385  2015-06-20                                                      
8386  2015-06-20  Kate Winslet in a smart ponytail and slinky bl...   
8387  2015-06-20                                                      

                         @timestamp  \
0     2015-09-22T00:00:00.000+08:00   
1     2015-09-22T00:00:00.000+08:00   
2     2015-09-22T00:00:00.000+08:00   
3     2015-09-22T00:00:00.000+08:00   
4     2015-09-22T00:00:00.000+08:00   
...                             ...   
8383  2015-06-20T00:00:00.000+08:00   
8384  2015-06-20T00:00:00.000+08:00   
8385  2015-06-20T00:00:00.000+08:00   
8386  2015-06-20T00:00:00.000+08:00   
8387  2015-06-20T00:00:00.000+08:00   

                                                   link        category  \
0     https://www.huffingtonpost.comhttp://recode.ne...           MEDIA   
1     https://www.huffingtonpost.com/entry/adorable-...         PARENTS   
2     https://www.huffingtonpost.com/entry/lawyers-c...           CRIME   
3     https://www.huffingtonpost.com/entry/climate-p...        POLITICS   
4     https://www.huffingtonpost.com/entry/hillary-c...        POLITICS   
...                                                 ...             ...   
8383  https://www.huffingtonpost.com/entry/awaiting-...   ENTERTAINMENT   
8384  https://www.huffingtonpost.com/entry/black-liv...        POLITICS   
8385  https://www.huffingtonpost.comhttp://www.usmag...   ENTERTAINMENT   
8386  https://www.huffingtonpost.com/entry/kate-wins...   ENTERTAINMENT   
8387  https://www.huffingtonpost.com/entry/inside-ou...  HEALTHY LIVING   

                                               headline  \
0     Report: Axel Springer Eyes Purchase Of Busines...   
1     Adorable Kid Has A Hard Time Blowing Out His B...   
2     Lawyers Can Keep Bras On While Entering Maine ...   
3     Activists Hope Pope Can Change Climate Convers...   
4         Hillary Clinton Comes Out Against Keystone XL   
...                                                 ...   
8383  Awaiting Interreflections: Peter Joseph's High...   
8384                       Black Lives and Gun Violence   
8385       Olivia Culpo Opens Up About Nick Jonas Split   
8386                     Kate Winslet in A Little Chaos   
8387  How 'Inside Out' Nailed The Science Of Kids' E...   

                                                authors  score  
0                                                          0.0  
1                                         Steven Hoffer    0.0  
2                                                          0.0  
3                                         Kate Sheppard    0.0  
4                    Kate Sheppard and Samantha-Jo Roth    0.0  
...                                                 ...    ...  
8383  Alex Simon, ContributorCo-editor, The Hollywoo...    0.0  
8384       Spencer Overton and Nina Vinik, Contributors    0.0  
8385                                                       0.0  
8386  Regina Weinreich, ContributorAuthor, 'Kerouac'...    0.0  
8387                                                       0.0  

[8388 rows x 8 columns]

In [224]:
s = Search(using=es, index='news_headlines')
a = A("cardinality", field="category")

s.aggs.metric('type_count', a)
s.execute()['aggregations']['type_count']

{'value': 41}

In [225]:
s = Search(using=es, index='news_headlines')
a = A('terms', field='category', size=200)
s.aggs.bucket('by_category', a)

s.execute()['aggregations']['by_category']['buckets']

[{'key': 'POLITICS', 'doc_count': 32739}, {'key': 'WELLNESS', 'doc_count': 17827}, {'key': 'ENTERTAINMENT', 'doc_count': 16058}, {'key': 'TRAVEL', 'doc_count': 9887}, {'key': 'STYLE & BEAUTY', 'doc_count': 9649}, {'key': 'PARENTING', 'doc_count': 8677}, {'key': 'HEALTHY LIVING', 'doc_count': 6694}, {'key': 'QUEER VOICES', 'doc_count': 6314}, {'key': 'FOOD & DRINK', 'doc_count': 6226}, {'key': 'BUSINESS', 'doc_count': 5937}, {'key': 'COMEDY', 'doc_count': 5175}, {'key': 'SPORTS', 'doc_count': 4884}, {'key': 'BLACK VOICES', 'doc_count': 4528}, {'key': 'HOME & LIVING', 'doc_count': 4195}, {'key': 'PARENTS', 'doc_count': 3955}, {'key': 'THE WORLDPOST', 'doc_count': 3664}, {'key': 'WEDDINGS', 'doc_count': 3651}, {'key': 'WOMEN', 'doc_count': 3490}, {'key': 'IMPACT', 'doc_count': 3459}, {'key': 'DIVORCE', 'doc_count': 3426}, {'key': 'CRIME', 'doc_count': 3405}, {'key': 'MEDIA', 'doc_count': 2815}, {'key': 'WEIRD NEWS', 'doc_count': 2670}, {'key': 'GREEN', 'doc_count': 2622}, {'key': 'WORLDPO

In [226]:
s = Search(using=es, index='news_headlines')\
    .query('match', **{"category": "ENTERTAINMENT"})
a = A("significant_text", field='headline', size=50)
s.aggs.metric('popular_in_entertainment', a)

len(s.execute().aggregations.popular_in_entertainment.buckets)

50

In [9]:
s = Search(using=es, index='news_headlines')\
    .query('match', category={'query':"ENTERTAINMENT"})

dsl_query_to_df(s)

date                                  short_description  \
0      2017-11-07  "My performance was not meant to be disrespect...   
1      2017-11-07  The company announced the decision hours after...   
2      2017-11-07  Let the "Jane the Virgin" star remind you to n...   
3      2017-11-07  You can take the girl out of Texas, but...! It...   
4      2017-11-06  This is why you should never buy him monogramm...   
...           ...                                                ...   
16053  2012-01-29  Bow Wow needs to hire himself a new accountant...   
16054  2012-01-29  Fox and American Idol snagged the exclusive wo...   
16055  2012-01-29  Nick Stahl found himself a little short on cas...   
16056  2012-01-28  Representation of the collective diaspora has ...   
16057  2012-01-28  "Sony Pictures will not be releasing The Girl ...   

                          @timestamp  \
0      2017-11-07T00:00:00.000+08:00   
1      2017-11-07T00:00:00.000+08:00   
2      2017-11-07T00:00:00.000+08:00   
3      2017-11-07T00:00:00.000+08:00   
4      2017-11-06T00:00:00.000+08:00   
...                              ...   
16053  2012-01-29T00:00:00.000+08:00   
16054  2012-01-29T00:00:00.000+08:00   
16055  2012-01-29T00:00:00.000+08:00   
16056  2012-01-28T00:00:00.000+08:00   
16057  2012-01-28T00:00:00.000+08:00   

                                                    link       category  \
0      https://www.huffingtonpost.com/entry/marilyn-m...  ENTERTAINMENT   
1      https://www.huffingtonpost.com/entry/los-angel...  ENTERTAINMENT   
2      https://www.huffingtonpost.com/entry/gina-rodr...  ENTERTAINMENT   
3      https://www.huffingtonpost.com/entry/jennifer-...  ENTERTAINMENT   
4      https://www.huffingtonpost.com/entry/sean-didd...  ENTERTAINMENT   
...                                                  ...            ...   
16053  https://www.huffingtonpost.comhttp://www.tmz.c...  ENTERTAINMENT   
16054  https://www.huffingtonpost.comhttp://insidetv....  ENTERTAINMENT   
16055  https://www.huffingtonpost.comhttp://www.tmz.c...  ENTERTAINMENT   
16056  https://www.huffingtonpost.com/entry/sundance-...  ENTERTAINMENT   
16057  https://www.huffingtonpost.com/entry/girl-with...  ENTERTAINMENT   

                                                headline  \
0      Marilyn Manson Defends Aiming Fake Assault Rif...   
1      Disney Ends LA Times Ban After Film Critics Th...   
2      Gina Rodriguez Tears Up As She Gets A Surprise...   
3      Jennifer Garner Has A Pet Chicken Named Regina...   
4      Sean 'Diddy' Combs Changes His Name Again, And...   
...                                                  ...   
16053    Bow Wow Has Tax Liens From 2006, 2008, And 2010   
16054  World Preview Of Madonna's 'Give Me All Your L...   
16055  'Terminator 3' Star Nick Stahl Arrested For No...   
16056  Sundance, Ice-T, and Shades of the American Ra...   
16057  'Girl With the Dragon Tattoo' India Release Ca...   

                                                 authors score  
0                                         Mary Papenfuss  None  
1                                          Hayley Miller  None  
2                                         Leigh Blickley  None  
3                                Jennifer Kline, AOL.com  None  
4                                             Ron Dicker  None  
...                                                  ...   ...  
16053                                                     None  
16054                                                     None  
16055                                                     None  
16056  Courtney Garcia, Contributor\nI tell stories a...  None  
16057                                                     None  

[16058 rows x 8 columns]

In [240]:
s = Search(using=es, index='news_headlines')\
    .query('match', headline={'query': "Khloe Kardashian Kendall Jenner", 'operator': 'and'})
    
dsl_query_to_df(s)

date                                  short_description  \
0  2017-12-04  The two of course asked Kim Kardashian what sh...   

                      @timestamp  \
0  2017-12-04T00:00:00.000+08:00   

                                                link       category  \
0  https://www.huffingtonpost.com/entry/kendall-j...  ENTERTAINMENT   

                                            headline     authors score  
0  Kendall Jenner, Khloe Kardashian Decide Whethe...  Ron Dicker  None

In [243]:
ms = MultiMatch(query="party planning", fields=["headline^2", "short_description"], type='phrase')

s = Search(using=es, index='news_headlines')\
    .query(ms)
    
dsl_query_to_df(s)

date                                  short_description  \
0  2015-02-18  "Oh, so this for you, then?" That's what my ne...   
1  2014-05-23  I recently stood in the middle of a madhouse. ...   
2  2014-01-09  How is a "mancation" different than a bachelor...   
3  2013-12-31  If you are opting out of the over-the-top part...   
4  2013-06-22  While it seems universally agreed that Paula D...   
5  2013-04-04  It's one thing if party planning is a source o...   

                      @timestamp  \
0  2015-02-18T00:00:00.000+08:00   
1  2014-05-23T00:00:00.000+08:00   
2  2014-01-09T00:00:00.000+08:00   
3  2013-12-31T00:00:00.000+08:00   
4  2013-06-22T00:00:00.000+08:00   
5  2013-04-04T00:00:00.000+08:00   

                                                link       category  \
0  https://www.huffingtonpost.com/entry/birthday-...        PARENTS   
1  https://www.huffingtonpost.com/entry/the-kids-...        PARENTS   
2  https://www.huffingtonpost.com/entry/5-ideas-f...         TRAVEL   
3  https://www.huffingtonpost.com/entry/new-years...  HOME & LIVING   
4  https://www.huffingtonpost.com/entry/bill-mahe...         COMEDY   
5  https://www.huffingtonpost.com/entry/less-fuss...      PARENTING   

                                            headline  \
0  Birthday Party Planning for the Recovering Per...   
1  This Is What a Kid's Birthday-Party-Planning E...   
2                    5 Ideas for Your Next Mancation   
3                 New Years Eve Party Planning Ideas   
4  Bill Maher Talks Paula Deen Controversy With '...   
5                                Less Fuss, More Fun   

                                             authors score  
0  Tracy Cutchlow, ContributorAuthor of "the cool...  None  
1  Jeff Bogle, ContributorAuthor of OutWithTheKid...  None  
2  U.S. News Travel, Contributor\nU.S. News & Wor...  None  
3  Lauren Nelson, Contributor\nFounder, Lauren-Ne...  None  
4                                                     None  
5  Christine Koh, Contributor\nMusic and brain sc...  None

In [16]:
s = Search(using=es, index='news_headlines').query('match_phrase', headline='Michelle Obama')

s.aggs.metric('category_mentions', A('terms', field='category', size=10))

s.execute().aggregations.category_mentions.buckets

print(s.to_dict())

{'query': {'match_phrase': {'headline': 'Michelle Obama'}}, 'aggs': {'category_mentions': {'terms': {'field': 'category', 'size': 10}}}}


In [19]:
q = Q('bool', must=[Q('match_phrase', **{"headline": "Michelle Obama"})], must_not=[Q('match', **{"category": "WEDDINGS"})])

s = Search(using=es, index='news_headlines').query(q)

dsl_query_to_df(s)['category'].unique()

array(['POLITICS', 'BLACK VOICES', 'PARENTS', 'WOMEN', 'HEALTHY LIVING',
       'ENTERTAINMENT', 'TASTE', 'ARTS & CULTURE', 'TRAVEL',
       'THE WORLDPOST', 'STYLE', 'IMPACT', 'COLLEGE', 'SPORTS',
       'LATINO VOICES', 'STYLE & BEAUTY', 'WELLNESS', 'PARENTING'],
      dtype=object)

In [26]:
q = Q('bool', must=Q('match_phrase', **{"headline": "Michelle Obama"}), filter=Q('range', **{"date": {"gte": "2014-03-25","lte": "2016-03-25"}})])

s = Search(using=es, index='news_headlines').query(q)

dsl_query_to_df(s).shape

(33, 8)

In [31]:
q = Q('bool', must=Q('match_phrase', **{"headline": "Michelle Obama"}), should=Q('match', **{"headline": "women", "headline": "Becoming", "headline": "empower"}))

s = Search(using=es, index='news_headlines').query(q)

dsl_query_to_df(s).shape

(207, 8)

In [36]:
s = Search(using=es, index='ecommerce_data')

s.aggs.metric("highest_unit_price", A('stats', field='UnitPrice'))

stat = s.execute().aggregations.highest_unit_price

stat.to_dict()

{'count': 539137,
 'min': 0.001,
 'max': 498.79,
 'avg': 3.6103066456206867,
 'sum': 1946449.894}

In [46]:
s = Search(using=es, index='ecommerce_data')

s.aggs.bucket('transactions_by_8_hrs', 'date_histogram', field='InvoiceDate', fixed_interval='8h', order={"_key": "desc"})
#s.aggs['per_category'].metric('clicks_per_category', 'sum', field='clicks')

s.execute().aggregations.transactions_by_8_hrs

{'buckets': [{'key_as_string': '12/1/2010 8:0', 'key': 12911...}

In [48]:
s = Search(using=es, index='ecommerce_data')

s.aggs.bucket('per_custom_price_ranges', 'range', field='UnitPrice', ranges=[{"to": 50},{"from": 50, "to": 200},{"from": 200}])
#s.aggs['per_category'].metric('clicks_per_category', 'sum', field='clicks')

s.execute().aggregations.per_custom_price_ranges

{'buckets': [{'key': '*-50.0', 'to': 50.0, 'doc_count': 5379...}

In [53]:
s = Search(using=es, index='ecommerce_data')

s.aggs.bucket('transactions_per_day', 'date_histogram', field='InvoiceDate', fixed_interval='1d')
s.aggs['transactions_per_day'].metric('daily_revenue', 'sum', script={"source": "doc['UnitPrice'].value * doc['Quantity'].value"})

s.execute().aggregations.transactions_per_day

{'buckets': [{'key_as_string': '12/1/2010 0:0', 'key': 12911...}

In [20]:
s.query('bool', filter=[Q('terms', tags=['search', 'python'])]).to_dict()

{'query': {'bool': {'must': [{'match_phrase': {'headline': 'Michelle Obama'}}],
   'must_not': [{'match': {'category': 'WEDDINGS'}}],
   'filter': [{'terms': {'tags': ['search', 'python']}}]}}}

In [182]:
s = Search(using=es, index='news_headlines')\
    .filter('range', **{'date':{"gte": "2015-06-20", "lte": "2015-09-22"}})\
    .params(preserve_order=True).sort("_score")

dsl_query_to_df_v3(s)

date                                  short_description  \
0     2015-09-22  German publishing giant Axel Springer is closi...   
1     2015-09-22                                 Dad to the rescue.   
2     2015-09-22  "I appreciate that [the sheriff] recognizes th...   
3     2015-09-22  The moral argument for climate action might fi...   
4     2015-09-22  After months of avoiding the subject, Clinton ...   
...          ...                                                ...   
8383  2015-06-20  In a time of great social strife and growing i...   
8384  2015-06-20  When states fail to pass laws that effectively...   
8385  2015-06-20                                                      
8386  2015-06-20  Kate Winslet in a smart ponytail and slinky bl...   
8387  2015-06-20                                                      

                         @timestamp  \
0     2015-09-22T00:00:00.000+08:00   
1     2015-09-22T00:00:00.000+08:00   
2     2015-09-22T00:00:00.000+08:00   
3     2015-09-22T00:00:00.000+08:00   
4     2015-09-22T00:00:00.000+08:00   
...                             ...   
8383  2015-06-20T00:00:00.000+08:00   
8384  2015-06-20T00:00:00.000+08:00   
8385  2015-06-20T00:00:00.000+08:00   
8386  2015-06-20T00:00:00.000+08:00   
8387  2015-06-20T00:00:00.000+08:00   

                                                   link        category  \
0     https://www.huffingtonpost.comhttp://recode.ne...           MEDIA   
1     https://www.huffingtonpost.com/entry/adorable-...         PARENTS   
2     https://www.huffingtonpost.com/entry/lawyers-c...           CRIME   
3     https://www.huffingtonpost.com/entry/climate-p...        POLITICS   
4     https://www.huffingtonpost.com/entry/hillary-c...        POLITICS   
...                                                 ...             ...   
8383  https://www.huffingtonpost.com/entry/awaiting-...   ENTERTAINMENT   
8384  https://www.huffingtonpost.com/entry/black-liv...        POLITICS   
8385  https://www.huffingtonpost.comhttp://www.usmag...   ENTERTAINMENT   
8386  https://www.huffingtonpost.com/entry/kate-wins...   ENTERTAINMENT   
8387  https://www.huffingtonpost.com/entry/inside-ou...  HEALTHY LIVING   

                                               headline  \
0     Report: Axel Springer Eyes Purchase Of Busines...   
1     Adorable Kid Has A Hard Time Blowing Out His B...   
2     Lawyers Can Keep Bras On While Entering Maine ...   
3     Activists Hope Pope Can Change Climate Convers...   
4         Hillary Clinton Comes Out Against Keystone XL   
...                                                 ...   
8383  Awaiting Interreflections: Peter Joseph's High...   
8384                       Black Lives and Gun Violence   
8385       Olivia Culpo Opens Up About Nick Jonas Split   
8386                     Kate Winslet in A Little Chaos   
8387  How 'Inside Out' Nailed The Science Of Kids' E...   

                                                authors  score  
0                                                          0.0  
1                                         Steven Hoffer    0.0  
2                                                          0.0  
3                                         Kate Sheppard    0.0  
4                    Kate Sheppard and Samantha-Jo Roth    0.0  
...                                                 ...    ...  
8383  Alex Simon, ContributorCo-editor, The Hollywoo...    0.0  
8384       Spencer Overton and Nina Vinik, Contributors    0.0  
8385                                                       0.0  
8386  Regina Weinreich, ContributorAuthor, 'Kerouac'...    0.0  
8387                                                       0.0  

[8388 rows x 8 columns]

In [160]:
s = Search(using=es, index="my_first_index")


dsl_query_to_df(s)

city  country  score
0   Paris   France    1.0
1  Vienna  Austria    1.0
2  London  England    1.0

In [158]:
s = Search(using=es, index="my_first_index")

list_of_respond = []
for doc in s.execute():
    list_of_respond.append({**doc.to_dict(), **{'score':doc.meta.score}})
    
pd.DataFrame(list_of_respond)

city  country  score
0   Paris   France    1.0
1  Vienna  Austria    1.0
2  London  England    1.0

In [170]:
s = Search(using=es, index="my_first_index")

#s = s.params(preserve_order=True).sort("_score")

for item in s.scan():
    print(item)
    print(item.meta)

<Hit(my_first_index/1): {'city': 'Paris', 'country': 'France'}>
{'index': 'my_first_index', 'id': '1', 'score': None, 'sort'...}
<Hit(my_first_index/uftds4EBga7skXllk854): {'city': 'Vienna', 'country': 'Austria'}>
{'index': 'my_first_index', 'id': 'uftds4EBga7skXllk854', 's...}
<Hit(my_first_index/3): {'city': 'London', 'country': 'England'}>
{'index': 'my_first_index', 'id': '3', 'score': None, 'sort'...}


In [127]:
for hit in s[:10].execute():
    print(hit)

<Hit(news_headlines/c8mD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'German publishi...}>
<Hit(news_headlines/dMmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'Dad to the resc...}>
<Hit(news_headlines/dcmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': '"I appreciate t...}>
<Hit(news_headlines/dsmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'The moral argum...}>
<Hit(news_headlines/d8mD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'After months of...}>
<Hit(news_headlines/eMmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'Um... are we se...}>
<Hit(news_headlines/ecmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'Arresting someo...}>
<Hit(news_headlines/esmD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'The makers of "...}>
<Hit(news_headlines/e8mD0oEBT6T2g4Ay3tda): {'date': '2015-09-22', 'short_description': 'She also took a...}>
<Hit(news_headlines

In [96]:
search_context = Search(using=es, index='sample_logs').query('match', Category='Tacks')

In [97]:
response = search_context.execute()

In [98]:
response['hits']['hits']

[]

In [88]:
search_context.to_dict()

{'query': {'match': {'Category': 'Tasks'}}}

In [76]:
for hit in response:
    print(hit.Category)

Tasks


In [81]:
s = search_context.query('query_string', query='Category:Tasks AND System-wide:description')

In [82]:
response = s.execute()

In [83]:
response

<Response: {}>

In [71]:
s.scan()

<generator object Search.scan at 0x7f0e1db0e0b0>

In [131]:
s = Search(using=es, index="my_first_index")

df = pd.DataFrame([hit.to_dict() for hit in s.scan()])

In [139]:
for hit in s.scan():
    print(hit.city)

Paris
Vienna
London


In [149]:
result = Search(using=es, index="my_first_index")

result = result.params(preserve_order=True).sort("_score")

In [150]:
for item in result.scan():
    print(item)

<Hit(my_first_index/1): {'city': 'Paris', 'country': 'France'}>
<Hit(my_first_index/uftds4EBga7skXllk854): {'city': 'Vienna', 'country': 'Austria'}>
<Hit(my_first_index/3): {'city': 'London', 'country': 'England'}>


In [143]:
df = pd.DataFrame((doc.to_dict() for doc in result))

In [144]:
df

city  country
0   Paris   France
1  Vienna  Austria
2  London  England

In [121]:
for hit in result:
    print(hit.meta.score)

1.0
1.0
1.0


In [157]:
for hit in Search(using=es, index="my_first_index").execute():
    print(hit.to_dict())
    print(hit.meta.score)

{'city': 'Paris', 'country': 'France'}
1.0
{'city': 'Vienna', 'country': 'Austria'}
1.0
{'city': 'London', 'country': 'England'}
1.0


In [155]:
hit_dict = hit.to_dict()
hit_dict['meta'] = hit.meta.to_dict()

In [156]:
hit_dict

{'city': 'London',
 'country': 'England',
 'meta': {'index': 'my_first_index', 'id': '3', 'score': 1.0}}